In [1]:
import pandas as pd
from sklearn import tree
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix, classification_report, accuracy_score
from IPython.display import Image
from six import StringIO
from sklearn.tree import export_graphviz
import pydotplus

In [2]:
df = pd.read_csv('../../datasets/train.csv', encoding="latin-1")
df.head()

Column1  CPSC_Case_Number Treatment_Date  Age  Sex  Race Other_Race  \
0   900763       180608221.0      5/29/2018   25    1   2.0        NaN   
1   762342       180109488.0       1/1/2018   70    2   1.0        NaN   
2   560150       170718633.0       7/5/2017   18    1   0.0        NaN   
3   464771       170429466.0       4/1/2017   17    2   1.0        NaN   
4   866180       180504499.0      4/27/2018   27    1   2.0        NaN   

   Hispanic  Body_Part  Diagnosis  ... Fire_Involvement  Alcohol  Drug  \
0       NaN       35.0       71.0  ...              0.0      NaN   NaN   
1       NaN       30.0       55.0  ...              0.0      NaN   NaN   
2       NaN       92.0       59.0  ...              0.0      NaN   NaN   
3       NaN       34.0       53.0  ...              0.0      NaN   NaN   
4       NaN       35.0       64.0  ...              0.0      NaN   NaN   

   Product_1  Product_2  Product_3  \
0     3265.0        0.0        0.0   
1      276.0        0.0        0.0   
2     3286.0        0.0        0.0   
3     4056.0        0.0        0.0   
4     1267.0        0.0        0.0   

                                           Narrative  Stratum   PSU   Weight  
0  25YOM PAIN TO KNEE WHEN LIFTING WEIGHTS       ...        L  42.0  55.4188  
1  70 YOF PT STATES SHE FELL IN HER KITCHEN & HIT...        M  16.0  78.3782  
2              18 YO M LAC FINGER-4-WHEELER ACCIDENT        V  17.0  16.1828  
3  17 YOF A SHELF FELL ONTO PT WRIST CAUSING A CO...        C  32.0   4.7570  
4  27 YOM HAS KNEE PX WHICH WORSENS WHILE PLAYING...        V  93.0  16.5919  

[5 rows x 26 columns]

In [3]:
inputs = df.filter(["Disposition", "Diagnosis", "Location"]).dropna()
inputs

Disposition  Diagnosis  Location
0               1.0       71.0       9.0
1               1.0       55.0       1.0
2               1.0       59.0       9.0
3               1.0       53.0       0.0
4               1.0       64.0       0.0
...             ...        ...       ...
702540          1.0       62.0       1.0
702541          1.0       53.0       1.0
702542          5.0       59.0       1.0
702543          1.0       62.0       1.0
702544          1.0       64.0       9.0

[702544 rows x 3 columns]

In [4]:
location = LabelEncoder()
diagnosis = LabelEncoder()
body_part = LabelEncoder()
inputs["location_n"] = location.fit_transform(inputs["Location"])
inputs["diagnosis_n"] = diagnosis.fit_transform(inputs["Diagnosis"])
inputs

Disposition  Diagnosis  Location  location_n  diagnosis_n
0               1.0       71.0       9.0           8           26
1               1.0       55.0       1.0           1           11
2               1.0       59.0       9.0           8           15
3               1.0       53.0       0.0           0            9
4               1.0       64.0       0.0           0           20
...             ...        ...       ...         ...          ...
702540          1.0       62.0       1.0           1           18
702541          1.0       53.0       1.0           1            9
702542          5.0       59.0       1.0           1           15
702543          1.0       62.0       1.0           1           18
702544          1.0       64.0       9.0           8           20

[702544 rows x 5 columns]

In [5]:
target = inputs["Disposition"]
target

0         1.0
1         1.0
2         1.0
3         1.0
4         1.0
         ... 
702540    1.0
702541    1.0
702542    5.0
702543    1.0
702544    1.0
Name: Disposition, Length: 702544, dtype: float64

In [6]:
inputs_n = inputs.drop(['Disposition', 'Diagnosis', 'Location'], axis='columns')
inputs_n

location_n  diagnosis_n
0                8           26
1                1           11
2                8           15
3                0            9
4                0           20
...            ...          ...
702540           1           18
702541           1            9
702542           1           15
702543           1           18
702544           8           20

[702544 rows x 2 columns]

In [7]:
model = tree.DecisionTreeClassifier()

In [8]:
X_train, X_test, y_train, y_test = train_test_split(inputs_n, target, test_size=0.2, random_state=1) # 80% training and 20% test

In [9]:
X_train, xval, y_train, yval = train_test_split(X_train, y_train, test_size=0.25, random_state=1) # 60% training and 20% 20% validation

In [10]:
model.fit(X_train,y_train)

DecisionTreeClassifier()

In [11]:
model.score(X_test,y_test)

0.890398479812681

In [12]:
predict = model.predict(X_test)
print("Accuracy Score: {}\n\nClassification Report:\n{}".format(accuracy_score(y_test, predict), classification_report(y_test, predict)))

Accuracy Score: 0.890398479812681

Classification Report:
              precision    recall  f1-score   support

         1.0       0.89      1.00      0.94    125110
         2.0       0.00      0.00      0.00      1153
         4.0       0.50      0.00      0.00     11414
         5.0       0.00      0.00      0.00      1050
         6.0       0.00      0.00      0.00      1690
         8.0       0.00      0.00      0.00        83
         9.0       0.00      0.00      0.00         9

    accuracy                           0.89    140509
   macro avg       0.20      0.14      0.13    140509
weighted avg       0.83      0.89      0.84    140509



/home/avasdowney/.local/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1308: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/avasdowney/.local/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1308: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/avasdowney/.local/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1308: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [17]:
confusion_matrix(y_test, model.predict(X_test))

array([[125108,      1,      1,      0,      0,      0,      0],
       [  1153,      0,      0,      0,      0,      0,      0],
       [ 11413,      0,      1,      0,      0,      0,      0],
       [  1050,      0,      0,      0,      0,      0,      0],
       [  1690,      0,      0,      0,      0,      0,      0],
       [    83,      0,      0,      0,      0,      0,      0],
       [     9,      0,      0,      0,      0,      0,      0]])

In [14]:
disposition = ['1', '2', '4', '5', '6', '8', '9']

In [15]:
feature_cols = ["Diagnosis", "Location"]
dot_data = StringIO()
export_graphviz(model, out_file=dot_data, filled=True, rounded=True, special_characters=True, feature_names = feature_cols,
    class_names=disposition)
graph = pydotplus.graph_from_dot_data(dot_data.getvalue())  
graph.write_png('../../outputs/location-disposition.png')
Image(graph.create_png())

dot: graph is too large for cairo-renderer bitmaps. Scaling by 0.927928 to fit

dot: graph is too large for cairo-renderer bitmaps. Scaling by 0.927928 to fit

